In [10]:
# 上诉代码没有共享模型
from scipy.spatial.distance import pdist, squareform
from scipy.spatial import KDTree
from numpy.linalg import norm
import torch
import torch.nn as nn
import torch.optim as optim
import copy
import os
from sklearn.metrics import f1_score,recall_score, accuracy_score, roc_auc_score,cohen_kappa_score,confusion_matrix,precision_score
from sklearn.preprocessing import LabelBinarizer
from sklearn.utils import shuffle
import random
from sklearn.cluster import KMeans
import torch
import torch.nn as nn
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.metrics import f1_score,recall_score, accuracy_score, roc_auc_score,cohen_kappa_score,confusion_matrix,precision_score
from sklearn.preprocessing import LabelBinarizer
from sklearn.preprocessing import StandardScaler
from sklearn.utils import shuffle
import copy
import os
import random
from sklearn.cluster import KMeans
from numpy.linalg import norm
from sklearn.neighbors import NearestNeighbors
import numpy as np
import random
from sklearn.cluster import KMeans
from sklearn.cluster import KMeans, DBSCAN, AgglomerativeClustering, OPTICS, MeanShift ,SpectralClustering
from sklearn_extra.cluster import KMedoids
from sklearn.mixture import GaussianMixture
import pandas as pd
from sklearn.utils import shuffle

import os
import torch
import hdbscan
import warnings
# 定义MLP模型
class MLP(nn.Module):
    def __init__(self, input_size, hidden_size, output_size):
        super(MLP, self).__init__()
        self.fc1 = nn.Linear(input_size, hidden_size)
        self.relu = nn.ReLU()
        self.fc2 = nn.Linear(hidden_size, output_size)

    def forward(self, x):
        x = self.fc1(x)
        x = self.relu(x)
        x = self.fc2(x)
        return x

class IncrementalSampling(object):
    def __init__(self,prototype_nums = 30,cluster_strategy = 'kmeans'):
        self.incremental_data_map = {}
        self.data  = np.array([])
        self.label = np.array([])
        self.k_value = prototype_nums
        # 2024 06 07
        self.cluster_strategy = cluster_strategy
    def split_current_data_by_class(self):
        """把当前轮的数据按类别划分"""
        # 获取唯一的类别标签
        current_unique_labels = np.unique(self.label)
        # 按类别分割当前轮获得的数据
        data_by_class = {}  # map {"label":[the data belong to the label]}
        for current_data_label in current_unique_labels:
            indices = np.where(self.label == current_data_label)[0]
            data_by_class[current_data_label] = self.data[indices]
        return data_by_class, current_unique_labels
    def data_combined(self):
        """把当前轮的数据，和类map中的数据进行合并"""
        current_data_map_by_class, current_unique_labels = self.split_current_data_by_class()
        # 考虑到有新类出现的情况
        # 如果current_unique_labels有新label,直接扩充incremental_data_map
        # 如果label 是incremental_data_map中已经有的，扩张incremental_data_map对应label中data的长度
        for new_data_label in current_unique_labels:
            if new_data_label in self.incremental_data_map:
                # 增量map中已经有这个标签的数据了，那就扩充这个数据
                self.incremental_data_map[new_data_label] = np.concatenate(
                    (self.incremental_data_map[new_data_label], current_data_map_by_class[new_data_label])
                )
            else:
                # 如果增量map中没有这个标签的的数据，就扩充增量map
                self.incremental_data_map[new_data_label] = current_data_map_by_class[new_data_label]
    def cluster_data(self,data, num_clusters):
        # ['kmeans','spectral','kmeans++','kmedoids','OPTICS','meanshift','gmm','hdbscan']
        # kmeans = KMeans(n_clusters=num_clusters,n_init='auto')
        cluster_centers = np.ndarray([])
        if self.cluster_strategy == 'kmeans':
            with warnings.catch_warnings():
            # KMeans(n_clusters=num_clusters,n_init='auto')
                # kmeans = KMeans(n_clusters=num_clusters,n_init='auto')
                kmeans = KMeans(n_clusters=num_clusters)
                kmeans.fit(data)
                cluster_centers = kmeans.cluster_centers_
        elif self.cluster_strategy == 'spectral':
            with warnings.catch_warnings():
                # 报错，小类样本太少，无法聚类
                print('cluster : spectral',{num_clusters})
                spectral = SpectralClustering(n_clusters=num_clusters, random_state=0, affinity='nearest_neighbors').fit(data)
                labels_spectral = spectral.labels_
                cluster_centers = np.array([data[labels_spectral == i].mean(axis=0) for i in range(num_clusters)])
                print(len(labels_spectral))
                print(len(cluster_centers))
        elif self.cluster_strategy.lower() == 'hdbscan':
            with warnings.catch_warnings():
                min_cluster_size = 2
                hdb = hdbscan.HDBSCAN(min_cluster_size=min_cluster_size).fit(data)
                labels_hdbscan = hdb.labels_
                cluster_centers = np.array([data[labels_hdbscan == i].mean(axis=0) for i in range(len(set(labels_hdbscan)) - (1 if -1 in labels_hdbscan else 0))])
        elif self.cluster_strategy.lower() == 'kmeans++' or self.cluster_strategy.lower() == 'kmeansplusplus' :
            with warnings.catch_warnings():
                kmeans_plus_plus = KMeans(n_clusters=num_clusters, init='k-means++', random_state=0).fit(data)
                cluster_centers = kmeans_plus_plus.cluster_centers_
        elif self.cluster_strategy.lower() =='kmedoids':
            with warnings.catch_warnings():
                # 有几个空簇
                print('cluster : spectral',{num_clusters})
                kmedoids = KMedoids(n_clusters=num_clusters-10, random_state=0).fit(data)
                labelxx = kmedoids.labels_
                cluster_centers = kmedoids.cluster_centers_
                print(len(cluster_centers))
        elif self.cluster_strategy.upper() =='OPTICS':
            with warnings.catch_warnings():
                min_samples = 2
                optics = OPTICS(min_samples=min_samples).fit(data)
                labels_optics = optics.labels_
                cluster_centers = np.array([data[labels_optics == i].mean(axis=0) for i in range(len(set(labels_optics)) - (1 if -1 in labels_optics else 0))])
                print(len(cluster_centers))
        elif self.cluster_strategy.lower() =='meanshift':
            with warnings.catch_warnings():
                bandwidth = 0.1
                mean_shift = MeanShift(bandwidth=bandwidth).fit(data)
                cluster_centers = mean_shift.cluster_centers_
        elif self.cluster_strategy.lower() =='gmm':
            with warnings.catch_warnings():
                gmm = GaussianMixture(n_components=num_clusters, random_state=0).fit(data)
                cluster_centers = gmm.means_  # 高斯混合模型的质心是每个成分的均值
        return  cluster_centers
    def reCludter(self):
        # incremental_data_map的大小进行压缩self.reCluster_instance_nums
        new_cluster = {}
        for label, data in self.incremental_data_map.items():
            if len(data) <= self.k_value:
                # 全部保存
                new_cluster[label] = data
            else:
                sampled_nums = self.k_value
                clusters = self.cluster_data(data = data, num_clusters=sampled_nums)
                new_cluster[label] = clusters
        self.incremental_data_map = new_cluster
    def compute_sampling_nums(self,combinde_map):
        # initialize
        min_length = float('inf')  # 初始化最小长度为正无穷大
        max_length = 0  # 初始化最大长度为0
        for label, data in combinde_map.items():
            data_length = len(data)
            if data_length < min_length:
                min_length = data_length
            if data_length > max_length:
                max_length = data_length
        return min_length, max_length
    def data_sampling(self,sampling_nums):
        resampling_data = []
        resampling_label = []
        for label, data in self.incremental_data_map.items():
            if len(data) > sampling_nums:
                # 那就是下采样了,不放回采样
                sampled_indices = random.sample(range(len(data)), sampling_nums)
                sampled_data = [data[i] for i in sampled_indices]
                resampling_data.extend(sampled_data)
                resampling_label.extend([label] * sampling_nums)
            elif len(data) == sampling_nums:
                # 直接复制
                resampling_data.extend(data)
                resampling_label.extend([label] * sampling_nums)
            else:
                # 上采样,保存原样本
                resampling_data.extend(data)
                # 随机有放回的找差额部分
                sampled_data = random.choices(data, k=(sampling_nums-len(data)))
                resampling_data.extend(sampled_data)
                resampling_label.extend([label] * sampling_nums)
        # 洗牌
        combined_data = list(zip(resampling_data, resampling_label))
        random.shuffle(combined_data)
        resampling_data, resampling_label = zip(*combined_data)
        return resampling_data,resampling_label
    def fit(self,incremental_prototype_map,data,label,sampling_strategy = "OverSampling"):
        self.incremental_data_map = incremental_prototype_map
        self.data = data
        self.label = label
        self.data_combined()
        resampling_data = []
        resampling_label = []
        min_length, max_length =self.compute_sampling_nums(self.incremental_data_map)
        if sampling_strategy.lower() == "oversampling":
            resampling_data,resampling_label = self.data_sampling(max_length)
        elif sampling_strategy.lower() == "downsampling":
            resampling_data,resampling_label = self.data_sampling(min_length)
        else:
            print("No sampling measures have been taken")
        self.reCludter()
        return resampling_data,resampling_label,self.incremental_data_map
# ['kmeans','spectral','kmeans++','kmedoids','OPTICS','meanshift','gmm']
class Incremental_sampling2(object):
    def __init__(self,save_prototype_nums = 30):
        self.save_prototype_nums = save_prototype_nums
        self.incremental_prototypes = {}
        self.data  = np.array([])
        self.label = np.array([])
        self.combined_map = {}
    def split_current_data_by_class(self):
        """把当前轮的数据按类别划分"""
        # 获取唯一的类别标签
        current_unique_labels = np.unique(self.label)
        # 按类别分割当前轮获得的数据
        data_by_class = {}  # map {"label":[the data belong to the label]}
        for current_data_label in current_unique_labels:
            indices = np.where(self.label == current_data_label)[0]
            data_by_class[current_data_label] = self.data[indices]
        return data_by_class, current_unique_labels
    def data_combined(self):
        """
        上一轮获得的数据原型和这一轮的新数据进行合并
        1.首先，按不同类别把数据和原型进行分开
        2.判断是不是新出现的类别的数据
            2.1、新类别数据,在原型map中直接扩展一个新类的map,{'新类':新类的数据}
            2.2、原先类别的数据,在对应类的数据上进行扩展，{'已有类':已有数据+新数据}
        """
        current_data_map_by_class, current_unique_labels = self.split_current_data_by_class()
        for new_data_label in current_unique_labels:
            if new_data_label in self.incremental_prototypes:
                # 增量map中已经有这个标签的数据了，那就扩充这个数据
                self.incremental_prototypes[new_data_label] = np.concatenate(
                    (self.incremental_prototypes[new_data_label], current_data_map_by_class[new_data_label])
                )
            else:
                # 如果增量map中没有这个标签的的数据，就扩充增量map
                self.incremental_prototypes[new_data_label] = current_data_map_by_class[new_data_label]
        self.combined_map = self.incremental_prototypes
    def cut_down_nearest_data_eu(self):
        """
        把每个类对应的原型中减去超出save_prototype_nums的样本
        判断规则：
            从离得最近的开始删除
        """
        for label in self.incremental_prototypes:
            data = self.incremental_prototypes[label]
            if len(data) > self.save_prototype_nums:
                # 计算成对距离
                pairwise_distances = squareform(pdist(data, 'euclidean'))
                np.fill_diagonal(pairwise_distances, np.inf)  # 将自身距离设置为无穷大，忽略自身距离

                while len(data) > self.save_prototype_nums:
                    # 找到距离最小的一对
                    min_dist_indices = np.unravel_index(np.argmin(pairwise_distances), pairwise_distances.shape)
                    # 保留一个样本，删除另一个
                    data = np.delete(data, min_dist_indices[1], axis=0)
                    # 从距离矩阵中删除对应的行和列
                    pairwise_distances = np.delete(pairwise_distances, min_dist_indices[1], axis=0)
                    pairwise_distances = np.delete(pairwise_distances, min_dist_indices[1], axis=1)

                # 使用简化后的数据更新原型
                self.incremental_prototypes[label] = data
    def cut_down_nearest_data_kdtree(self):
        """
        把每个类对应的原型中减去超出save_prototype_nums的样本
        判断规则：
            从离得最近的开始删除
        """
        for label in self.incremental_prototypes:
            # self.incremental_prototypes 在这之前已经和新数据合并了
            data = self.incremental_prototypes[label]
            if len(data) > self.save_prototype_nums:
                while len(data) > self.save_prototype_nums:
                    # 建立 KD 树
                    kdtree = KDTree(data)
                    # 查询每个点的最近邻
                    distances, indices = kdtree.query(data, k=2)  # k=2 因为第一个最近邻是点本身

                    # 找到最近的两个点
                    min_dist_idx = np.argmin(distances[:, 1])  # distances[:, 1] 是每个点的最近邻距离
                    nearest_idx = indices[min_dist_idx, 1]

                    # 删除其中一个点
                    data = np.delete(data, nearest_idx, axis=0)

                # 使用简化后的数据更新原型
                self.incremental_prototypes[label] = data
    def cut_down_nearest_data_nn(self):
        """
        把每个类对应的原型中减去超出save_prototype_nums的样本
        判断规则：
            使用批量删除
        """
        for label in self.incremental_prototypes:
            data = self.incremental_prototypes[label]
            if len(data) > self.save_prototype_nums:
                while len(data) > self.save_prototype_nums:
                    # 建立 NearestNeighbors 模型
                    nbrs = NearestNeighbors(n_neighbors=2, algorithm='auto').fit(data)
                    distances, indices = nbrs.kneighbors(data)

                    # 找到距离最小的一对
                    min_dist_idx = np.argmin(distances[:, 1])
                    nearest_idx = indices[min_dist_idx, 1]

                    # 批量删除，尽量减少删除操作次数
                    delete_indices = [min_dist_idx, nearest_idx]
                    data = np.delete(data, delete_indices, axis=0)

                # 使用简化后的数据更新原型
                self.incremental_prototypes[label] = data
    def cut_down_nearest_data(self):
        """
        把每个类对应的原型中减去超出save_prototype_nums的样本
        判断规则：
            保留距离最远的样本
        """
        for label in self.incremental_prototypes:
            data = self.incremental_prototypes[label]
            if len(data) > self.save_prototype_nums:
                # 计算成对距离矩阵
                pairwise_distances = squareform(pdist(data, 'euclidean'))

                # 对距离矩阵进行排序，获取距离最远的样本索引
                farthest_indices = np.argsort(-pairwise_distances.sum(axis=1))

                # 保留距离最远的前save_prototype_nums个样本
                keep_indices = farthest_indices[:self.save_prototype_nums]
                data = data[keep_indices]

                # 使用简化后的数据更新原型
                self.incremental_prototypes[label] = data
    def compute_sampling_nums(self,combined_map):
        # initialize
        min_length = float('inf')  # 初始化最小长度为正无穷大
        max_length = 0  # 初始化最大长度为0
        for label, data in combined_map.items():
            data_length = len(data)
            if data_length < min_length:
                min_length = data_length
            if data_length > max_length:
                max_length = data_length
        return min_length, max_length
    def triplet_sampling(self, num_cluster, n_neighbors=5, randomOr=True, len_lim=True):
        """Triplets 数据采样"""
        gen_x = []
        gen_y = []
        for label in self.incremental_prototypes:
            data_min = self.incremental_prototypes[label]
            if len(data_min) < num_cluster:
                size = num_cluster - len(data_min)
                weight = np.ones(len(data_min))
                # 收集多数类样本
                data_maj = np.vstack([self.incremental_prototypes[l] for l in self.incremental_prototypes if l != label])
                gen_x_c, gen_y_c = self._sample_one(data_min, data_maj, label, size, weight, n_neighbors, randomOr, len_lim)
                gen_x += gen_x_c
                gen_y += gen_y_c
        resampling_data = []
        resampling_label = []
        for label in self.combined_map: # incremental_prototypes样本太少了，只是为了生成样本用的
            data = self.incremental_prototypes[label]
            resampling_data.append(data)
            resampling_label.extend([label] * len(data))
        resampling_data = np.vstack(resampling_data)
        resampling_label = np.array(resampling_label)
        if len(gen_x) > 0:
            gen_x = np.vstack(gen_x)
            gen_y = np.array(gen_y)
            resampling_data = np.concatenate((resampling_data, gen_x), axis=0)
            resampling_label = np.concatenate((resampling_label, gen_y), axis=0)
        # 洗牌
        combined_data = list(zip(resampling_data, resampling_label))
        random.shuffle(combined_data)
        resampling_data, resampling_label = zip(*combined_data)
        return resampling_data,resampling_label
    def _sample_one(self, data_min, data_maj, label, size, weight, n_neighbors, randomOr, len_lim):
        gen_x = []
        gen_y = []
        if size == 0: return gen_x, gen_y

        min_idxs = np.arange(len(data_min))
        nbrs = NearestNeighbors(n_neighbors=n_neighbors).fit(data_maj)
        _, indices = nbrs.kneighbors(data_min)

        for j in np.random.choice(len(min_idxs), size, p=weight / weight.sum()):
            tp1 = data_min[min_idxs[j]]
            tp2 = data_maj[indices[j][:5]].mean(axis=0)
            tp3_ord = np.random.randint(n_neighbors)
            tp3 = data_maj[indices[j][tp3_ord]]
            if (tp2 == tp1).all():
                gen_x.append(tp1)
                gen_y.append(label)
                continue

            offset = tp3 - tp2
            offset_norm = norm(offset)
            if offset_norm == 0:
                continue

            tp1_tp2_norm = norm(tp1 - tp2)
            if tp1_tp2_norm == 0:
                continue

            if len_lim: offset = offset * min(1, tp1_tp2_norm / offset_norm)
            coef = np.random.rand() if randomOr else 1.0
            new_x = tp1 + coef * offset
            gen_x.append(new_x)
            gen_y.append(label)

        return gen_x, gen_y

    def random_sampling(self,num_cluster,sampling_strategy):
        """
        这里需要对数据采样
        首先遍历self.incremental_prototypes ,每个类
        以及每个类的数据的长度
        然后比较每个类的数据的长度和num_cluster之间的差距
        差额部分使用triplets的核心算法对齐进行生成样本
        """
        resampling_data = []
        resampling_label = []
        if sampling_strategy == "ros-p":
            # 随机上采样，差额数据从原型数据中随机复制
            for label, data in self.combined_map.items():
                if len(data) < num_cluster:  # 需要上采样的数据的条件
                    prototype_data = self.incremental_prototypes[label]
                    sampling_nums = num_cluster - len(data)

                    if len(prototype_data) < sampling_nums:
                        sampled_data = []
                        while len(sampled_data) < sampling_nums:
                            # 原型中样本还没有sampling_nums多时，直接复制原型中的数据
                            needed = sampling_nums - len(sampled_data)
                            sampled_indices = random.sample(range(len(prototype_data)), min(needed, len(prototype_data)))
                            sampled_data.extend([prototype_data[i] for i in sampled_indices])
                    else:
                        sampled_indices = random.sample(range(len(prototype_data)), sampling_nums)
                        sampled_data = [prototype_data[i] for i in sampled_indices]

                    resampling_data.extend(data)
                    resampling_label.extend([label] * len(data))
                    resampling_data.extend(sampled_data)
                    resampling_label.extend([label] * sampling_nums)
                elif len(data) == num_cluster:
                    resampling_data.extend(data)
                    resampling_label.extend([label] * len(data))
        elif sampling_strategy == "ros-h" :
            # 随机上采样，从混合数据中采样差额数据
            for label, data in self.combined_map.items():
                data_len = len(data)
                if data_len < num_cluster:
                    # 那就是下采样了,不放回采样
                    sampling_nums = num_cluster-data_len
                    if data_len < sampling_nums:
                        sampled_data = []
                        while len(sampled_data) < sampling_nums:
                            # 原型中样本还没有sampling_nums多时，直接复制原型中的数据
                            needed = sampling_nums - len(sampled_data)
                            sampled_indices = random.sample(range(data_len), min(needed, data_len))
                            sampled_data.extend([data[i] for i in sampled_indices])
                    else:
                        sampled_indices = random.sample(range(data_len), sampling_nums)
                        sampled_data = [data[i] for i in sampled_indices]
                    resampling_data.extend(data)
                    resampling_label.extend([label] * len(data))
                    resampling_data.extend(sampled_data)
                    resampling_label.extend([label] * sampling_nums)
                elif len(data) == num_cluster:
                    # 直接复制
                    resampling_data.extend(data)
                    resampling_label.extend([label] * len(data))
        # 洗牌
        combined_data = list(zip(resampling_data, resampling_label))
        random.shuffle(combined_data)
        resampling_data, resampling_label = zip(*combined_data)
        return resampling_data,resampling_label
    def fit(self,new_data,new_data_label,last_round_prototype,sampling_strategy='tpl'):
        self.incremental_prototypes = last_round_prototype
        self.data = new_data
        self.label = new_data_label
        self.data_combined()
        resampling_data = []
        resampling_label = []
        min_length, max_length =self.compute_sampling_nums(self.incremental_prototypes)
        if sampling_strategy.lower() == "tpl":
            resampling_data,resampling_label = self.triplet_sampling(max_length)
        elif sampling_strategy.lower() == "ros-p":
            # rest data copied from prototype
            resampling_data,resampling_label = self.random_sampling(max_length,sampling_strategy = "ros-p")
            print('use ros p')
        elif sampling_strategy.lower() == "ros-h":
            # rest data copied from hybrid data(combined data)
            resampling_data,resampling_label = self.random_sampling(max_length,sampling_strategy = "ros-h")
            print('use ros h')
        return resampling_data,resampling_label,self.incremental_prototypes
class Triplets(object):
    def __init__(self, n_neighbors=5, random=True, len_lim=True, **kwargs):
        self.n_neighbors = n_neighbors
        self.random = random
        self.len_lim = len_lim

    def fit_resample(self, x, y):
        strategy = self._sample_strategy(y)
        self.n_neighbors = max(self.n_neighbors, self.counts.max() // self.counts.min())

        gen_x = []
        gen_y = []
        # 这里的代码平衡状态会报错
        for c, size in enumerate(strategy):
            if size == 0: continue
            weight = self._weights(x, y, c)
            gen_x_c, gen_y_c = self._sample_one(x, y, c, size, weight)
            gen_x += gen_x_c
            gen_y += gen_y_c

        # 为了这个方法在平衡状态下不报错，我们特地在这里加了这段代码
        # To prevent errors in this method when in a balanced state, we intentionally added this code block
        if len(gen_x)==0:
            return x,y
        gen_x = np.vstack(gen_x)
        gen_y = np.array(gen_y)
        return np.concatenate((x, gen_x), axis=0), np.concatenate((y, gen_y), axis=0)

    def _sample_strategy(self, y):
        _, self.counts = np.unique(y, return_counts=True)
        return max(self.counts) - self.counts

    def _weights(self, x, y, c):
        return np.ones(self.counts[c])

    def _sample_one(self, x, y, c, size, weight):
        gen_x = []
        gen_y = []
        if size == 0: return gen_x, gen_y

        # get the indices of minority and majority instances
        min_idxs = np.where(y == c)[0]
        maj_idxs = np.where(y != c)[0]

        # find nearest majority neighbors for each minority instance
        nbrs = NearestNeighbors(n_neighbors=self.n_neighbors).fit(x[maj_idxs])
        _, indices = nbrs.kneighbors(x[min_idxs])

        # generate synthetic data
        for j in np.random.choice(len(min_idxs), size, p=weight / weight.sum()):
            tp1 = x[min_idxs[j]]
            tp2 = x[maj_idxs[indices[j][:5]]].mean(axis=0)
            # tp3_ord = np.random.randint(1, self.n_neighbors)
            tp3_ord = np.random.randint(self.n_neighbors)
            tp3 = x[maj_idxs[indices[j][tp3_ord]]]
            if (tp2 == tp1).all():
                gen_x.append(tp1)
                gen_y.append(c)
                continue

            offset = tp3 - tp2
            if self.len_lim: offset = offset * min(1, norm(tp1 - tp2) / norm(offset))
            coef = np.random.rand() if self.random is True else 1.0
            new_x = tp1 + coef * offset
            gen_x.append(new_x)
            gen_y.append(c)
        return gen_x, gen_y

def train_model_FedAvg_local(input_model,X_train_tensor, y_train_tensor, num_epochs):
    losses =[]
    model = input_model# copy.deepcopy(input_model)
    optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.CrossEntropyLoss()
    model.train()
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        loss.backward()
        optimizer.step()
        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())  # 将每次训练的损失值添加到列表中

    return losses
def train_model_FedProx_local(input_model, X_train_tensor, y_train_tensor, num_epochs):
    mu = 0.1
    # because last round trained global model replaced local model,
    # that in this round the first local model is last round global model
    losses =[]
    model = input_model# copy.deepcopy(input_model)
    optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.CrossEntropyLoss()
    global_weights = copy.deepcopy(list(model.parameters()))
    # not use deepcopy ,because model as parameter transport in this ,update model also update model
    # current_local_model = cmodel
    # model.train()
    # for epoch in range(num_epochs):
    model.train()
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        # FedProx
        prox_term = 0.0
        for p_i, param in enumerate(model.parameters()):
                prox_term += (mu / 2) * torch.norm((param - global_weights[p_i])) ** 2
        loss += prox_term

        loss.backward()
        optimizer.step()
        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())  # 将每次训练的损失值添加到列表中
    #     total_loss = 0.0
    #     for step,(x,y) in enumerate(zip(X_train_tensor,y_train_tensor)):
    #         # current_local_model.train()
    #         output = model(x) # current_local_model(x)
    #         loss = criterion(output, y)
    #         total_loss+=loss.item()
    #         optimizer.zero_grad()
    #
    #         # fedprox
    #         prox_term = 0.0
    #         for p_i, param in enumerate(model.parameters()):
    #             prox_term += (mu / 2) * torch.norm((param - global_weights[p_i])) ** 2
    #         loss += prox_term
    #         loss.backward()
    #         optimizer.step()
    #     losses.append(total_loss)
    #     if epoch % 10 == 0:
    #         print(f"Epoch [{epoch+1}/{num_epochs}], Epoch Total Loss: {total_loss:.4f}")
    return losses

def train_model_FedNova_local(input_model,X_train_tensor, y_train_tensor, num_epochs):
    # because last round trained global model replaced local model,
    # that in this round the first local model is last round global model
    losses =[]
    model = input_model
    optimizer = torch.optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.CrossEntropyLoss()
    global_weights = copy.deepcopy(input_model.state_dict())
    tau = 0
    rho = 0.9
    model.train()
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        tau +=len(y_train_tensor)
        loss.backward()
        optimizer.step()
        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())
    # for epoch in range(num_epochs):
    #     total_loss = 0.0
    #     for step,(x,y) in enumerate(zip(X_train_tensor,y_train_tensor)):
    #         # current_local_model.train()
    #         # model.train()
    #         output = model(x) # current_local_model(x)
    #         loss = criterion(output, y)
    #         total_loss+=loss.item()
    #         optimizer.zero_grad()
    #         loss.backward()
    #         optimizer.step()
    #         tau +=1
    #     losses.append(total_loss)
    #     if epoch % 10 == 0:
    #         print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {total_loss:.4f}")
    coeff = (tau - rho * (1 - pow(rho, tau)) / (1 - rho)) / (1 - rho)
    state_dict = model.state_dict()
    norm_grad = copy.deepcopy(global_weights)
    for key in norm_grad:
        norm_grad[key] = torch.div(global_weights[key] - state_dict[key], coeff)

    return losses, coeff, norm_grad,len(X_train_tensor)
# 定义模型参数共享函数
def share_params(model):
    params = model.state_dict()
    # return {k: v.clone().detach().requires_grad_(True) for k, v in params.items()}
    return {k: v.clone().detach().requires_grad_(False) for k, v in params.items()}

# # 定义模型参数聚合函数
def aggregate_params(params_list):
    aggregated_params = {}
    for key in params_list[0].keys():
        # 将参数转换为张量进行处理
        params_tensors = [params[key].clone().detach().float() for params in params_list]
        # 聚合参数
        aggregated_params[key] = sum(params_tensors) / len(params_tensors)
    return aggregated_params
def test(global_model,X_test,y_test):
    # 在全局模型上进行测试
    with torch.no_grad():
        X_test_tensor = torch.FloatTensor(X_test)
        y_test_tensor = torch.LongTensor(y_test)
        outputs = global_model(X_test_tensor)
        _, predicted = torch.max(outputs, 1)
        accuracy = (predicted == y_test_tensor).sum().item() / len(y_test_tensor)
        print(f"Test Accuracy: {accuracy * 100:.2f}%")

        # 计算度量
        predictions = predicted.numpy() # 将张量转换为 NumPy 数组并去除零维数组
        true_labels = y_test_tensor.numpy()  # 将张量转换为 NumPy 数组并去除零维数组
        precision = precision_score(true_labels,predictions,zero_division=0.0,average=None)
        precision_micro = precision_score(true_labels,predictions,zero_division=0.0,average='micro')
        precision_macro = precision_score(true_labels,predictions,zero_division=0.0,average='macro')
        # recall
        recalls = recall_score(true_labels,predictions,zero_division=0.0,average=None)
        recalls_micro =recall_score(true_labels,predictions,zero_division=0.0,average='micro')
        recalls_macro =recall_score(true_labels,predictions,zero_division=0.0,average='macro')
        f1_scores = f1_score(true_labels, predictions, average=None)
        acc = accuracy_score(true_labels, predictions)
        kappa = cohen_kappa_score(true_labels,predictions)
        conf_matrix = confusion_matrix(true_labels,predictions)
        # 计算所有类别乘积的几何平均值作为 G-mean
        g_mean_all= np.power(np.prod(recalls), 1 / len(recalls))
        # AUC
        lb = LabelBinarizer()
        lb.fit(true_labels)
        true_labels_bin = lb.transform(true_labels)
        predictions_bin = lb.transform(predictions)
        auc = roc_auc_score(true_labels_bin, predictions_bin, average='weighted', multi_class='ovr')
        metrics = {
            'recall':recalls,
            'recall_micro':recalls_micro,
            'recall_macro':recalls_macro,
            'precision':precision,
            'precision_micro':precision_micro,
            'precision_macro':precision_macro,
            'f1_score':f1_scores,
            'g_mean':g_mean_all,
            'acc':acc,
            'auc':auc,
            'kappa':kappa,
            'confusion_matrix':conf_matrix
        }
        return metrics

def save_loss(loss_list,client_id,round_id,save_loss_path):
    if not os.path.exists(save_loss_path):
        os.makedirs(save_loss_path)
    # 构建文件路径
    file_path = os.path.join(save_loss_path, f"client_{client_id}.csv")

    if os.path.exists(file_path):
        # 如果文件存在，加载现有的 CSV 文件为 DataFrame
        df = pd.read_csv(file_path)
    else:
        # 如果文件不存在，直接创建新的 DataFrame
        df = pd.DataFrame()

    # 将损失值添加到 DataFrame 中
    column_name = f'round_{round_id}'
    df[column_name] = loss_list

    # 将 DataFrame 保存为 CSV 文件
    df.to_csv(file_path, index=False)
def save_model(global_model,round_id,save_model_path):
    if not os.path.exists(save_model_path):
        os.makedirs(save_model_path)
    model_path = os.path.join(save_model_path,f'round_{round_id}_gm.pt')
    torch.save(global_model,model_path)

def save_metrics(title, rounds, metrics, save_folder):
    if not os.path.exists(save_folder):
        os.makedirs(save_folder)

    file_name = f"{title}.csv"
    file_path = os.path.join(save_folder, file_name)
    # print(file_path)
    recalls = metrics['recall']
    class_nums = len(recalls)
    # 检查文件是否存在
    if os.path.exists(file_path):
        # 如果文件存在，加载现有的 Excel 文件为 DataFrame
        df = pd.read_csv(file_path)
    else:
        # 如果文件不存在，直接创建新的 DataFrame
        columns = [
        'rounds', 'accuracy', 'auc', 'kappa', 'g_mean', 'recall_micro', 'precision_micro',
        'recall_macro', 'precision_macro'
        ]
        df = pd.DataFrame(columns=columns)
        for i in range(class_nums):  # 动态生成 f1-score 相关列名
            columns.append(f'f1_score_{i}')
            columns.append(f'recall_{i}')
            columns.append(f'precession_{i}')

    data = {
        'rounds': rounds,
        'accuracy': metrics['acc'],
        'auc': metrics['auc'],
        'kappa': metrics['kappa'],
        'g_mean':metrics['g_mean'],
        'recall_micro':metrics['recall_micro'],
        'precision_micro':metrics['precision_micro'],
        'recall_macro':metrics['recall_macro'],
        'precision_macro':metrics['precision_macro']
    }
    # 添加每个类别的 F1-score、G-mean 和 Recall 到 data 中
    for i in range(class_nums):  #类别数
        data[f'recall_{i}'] = metrics['recall'][i]
        data[f'precision_{i}'] = metrics['precision'][i]
        data[f'f1_score_{i}'] = metrics['f1_score'][i]
    # 创建新行并追加到 DataFrame
    new_row = pd.DataFrame(data, index=[0])
    df = pd.concat([df, new_row], ignore_index=True)

    # 将 DataFrame 保存为 Excel 文件
    df.to_csv(file_path, index=False)

from imblearn.over_sampling import SMOTE,RandomOverSampler,SMOTENC,SMOTEN,ADASYN,BorderlineSMOTE,KMeansSMOTE,SVMSMOTE
from imblearn.under_sampling import ClusterCentroids,RandomUnderSampler,NearMiss,TomekLinks,EditedNearestNeighbours,RepeatedEditedNearestNeighbours,AllKNN,CondensedNearestNeighbour,OneSidedSelection,NeighbourhoodCleaningRule,InstanceHardnessThreshold
from imblearn.combine import SMOTEENN,SMOTETomek
# SMOTE,ROS,SMOTENC,SMOTEN,ADASYN,BorderlineSMOTE1,BorderlineSMOTE2,KMeansSMOTE,SVMSMOTE
# ClusterCentroids,RUS,NearMiss1,NearMiss2,NearMiss2,TomekLinks,ENN,RENN,AllKNN,CNN,OSS,NC,IHT
# SMOTEENN,SMOTETomek
def data_sampling(raw_X,raw_y,sampling_strategy):
    if sampling_strategy.upper() == 'NO' :
        return raw_X,raw_y
    # overSampling
    elif sampling_strategy.upper() == 'SMOTE': # overSampling
        """
            1.对于样本x ,按照欧氏距离找到离其距离最近的K个近邻样本
            2.确定采样比例，然后从K个近邻中选择x_n
            3.公式 x_new = x + rand(0,1)*(x_n-x)
        """
        smote = SMOTE( random_state=42)
        X_resampled, y_resampled = smote.fit_resample(raw_X,raw_y)
        return X_resampled, y_resampled
    elif sampling_strategy == "RandomOverSampler" or sampling_strategy.upper()=='ROS': # overSampling
        ros = RandomOverSampler(random_state=1)
        ros_data,ros_label = ros.fit_resample(raw_X,raw_y)
        return ros_data,ros_label
    elif sampling_strategy.upper() == 'SMOTENC':    # overSampling
        smotenc = SMOTENC(random_state=1,categorical_features=[0])
        smotenc_data,smotenc_label = smotenc.fit_resample(raw_X,raw_y)
        return smotenc_data,smotenc_label
    elif sampling_strategy.upper() == 'SMOTEN': # overSampling
        smoten = SMOTEN(random_state=1)
        smoten_data,smoten_label = smoten.fit_resample(raw_X,raw_y)
        return smoten_data,smoten_label
    elif sampling_strategy.upper() =='ADASYN':
        adasyn = ADASYN(random_state=1)
        adasyn_data,adasyn_label = adasyn.fit_resample(raw_X,raw_y)
        return adasyn_data,adasyn_label
    elif sampling_strategy == 'BorderlineSMOTE1' or sampling_strategy.upper()=='BSMOTE1':
        bsmote1 = BorderlineSMOTE(kind='borderline-1',random_state=1)
        bsmote1_data,bsmote1_label = bsmote1.fit_resample(raw_X,raw_y)
        return bsmote1_data,bsmote1_label
    elif sampling_strategy == 'BorderlineSMOTE2'or sampling_strategy.upper()=='BSMOTE2':
        bsmote2 = BorderlineSMOTE(kind='borderline-2',random_state=1)
        bsmote2_data,bsmote2_label = bsmote2.fit_resample(raw_X,raw_y)
        return bsmote2_data,bsmote2_label
    elif sampling_strategy == 'KMeansSMOTE' or sampling_strategy.upper() == 'KSMOTE':
        kmeanssmote = KMeansSMOTE(random_state=1)
        kmeanssmote_data,kmeanssmote_label = kmeanssmote.fit_resample(raw_X,raw_y)
        return kmeanssmote_data,kmeanssmote_label
    elif sampling_strategy == 'SVMSMOTE':
        svmsmote = SVMSMOTE(random_state=1)
        svmsmote_data,svmsmote_label = svmsmote.fit_resample(raw_X,raw_y)
        return svmsmote_data,svmsmote_label
    # downSampling
    elif sampling_strategy == 'ClusterCentroids': # down-sampling,generate
        clustercentroids = ClusterCentroids(random_state=1)
        clustercentroids_data,clustercentroids_label = clustercentroids.fit_resample(raw_X,raw_y)
        return clustercentroids_data,clustercentroids_label
    elif sampling_strategy=='RandomUnderSampler' or sampling_strategy.upper()=='RUS':
        rus = RandomUnderSampler(random_state=1)
        rus_data,rus_label = rus.fit_resample(raw_X,raw_y)
        return rus_data,rus_label
    elif sampling_strategy.upper() =='NEARMISS1':
        # 在k个少数类别样本中，选择出与他们-平均距离最近的多数类样本-进行保存
        nearmiss1 = NearMiss(version=1)
        nearmiss1_data,nearmiss1_label = nearmiss1.fit_resample(raw_X,raw_y)
        return nearmiss1_data,nearmiss1_label
    elif sampling_strategy.upper() =='NEARMISS2':
        # 选择K个距离最远的少数类别样本，然后根据这些样本选出的"平均距离最近"的样本进行保存
        nearmiss2 = NearMiss(version=2)
        nearmiss2_data,nearmiss2_label = nearmiss2.fit_resample(raw_X,raw_y)
        return nearmiss2_data,nearmiss2_label
    elif sampling_strategy.upper() =='NEARMISS3':
        # 1、对于每一个少数类别样本，保留其K个最近邻多数类样本；2、把到K个少数样本平均距离最大的多数类样本保存下来。
        nearmiss3 = NearMiss(version=3)
        nearmiss3_data,nearmiss3_label = nearmiss3.fit_resample(raw_X,raw_y)
        return nearmiss3_data,nearmiss3_label
    elif sampling_strategy == 'TomekLinks' or sampling_strategy.upper()=='TOMEK':
        # 它需要计算每个样本之间的距离，然后把互为最近邻且类别不同的一对样本拿出来，根据需求的选择将这一对数据进行剔除 or 把多数类样本剔除
        tomelink = TomekLinks(sampling_strategy='all')#sampling_strategy='all'表示全部删除，'auto'表示只删除多数类
        tomelink_data,tomelink_label = tomelink.fit_resample(raw_X,raw_y)
        return tomelink_data,tomelink_label
    elif sampling_strategy == 'EditedNearestNeighbours' or sampling_strategy.upper() == 'ENN':
        ENN = EditedNearestNeighbours()
        ENN_data,ENN_label = ENN.fit_resample(raw_X,raw_y)
        return ENN_data,ENN_label
    elif sampling_strategy == 'RepeatedEditedNearestNeighbours' or sampling_strategy.upper() == 'RENN':
        RENN = RepeatedEditedNearestNeighbours()
        RENN_data,RENN_label = RENN.fit_resample(raw_X,raw_y)
        return RENN_data,RENN_label
    elif sampling_strategy =='AllKNN':
        ## ENN的改进版本，和RepeatedEditedNearestNeighbours一样，会多次迭代ENN 算法，不同之处在于，他会每次增加KNN的K值
        allknn = AllKNN()
        allknn_data,allknn_label = allknn.fit_resample(raw_X,raw_y)
        return allknn_data,allknn_label
    elif sampling_strategy == 'CondensedNearestNeighbour'or sampling_strategy.upper() == 'CNN':
        ## 如果有样本无法和其他多数类样本聚类到一起，那么说明它极有可能是边界的样本，所以将这些样本加入到集合中
        CNN = CondensedNearestNeighbour(random_state=1)
        CNN_data,CNN_label = CNN.fit_resample(raw_X,raw_y)
        return CNN_data,CNN_label
    elif sampling_strategy == 'OneSidedSelection' or sampling_strategy.upper() == 'OSS':
        # OneSidedSelection = tomekLinks + CondensedNearestNeighbour,先使用自杀式的方式把大类数据中的其他值剔除，然后再使用CondensedNearestNeighbour的下采样
        OSS = OneSidedSelection(random_state=1)
        OSS_data,OSS_label = OSS.fit_resample(raw_X,raw_y)
        return OSS_data,OSS_label
    elif sampling_strategy == 'NeighbourhoodCleaningRule'or sampling_strategy.upper() == 'NC':
        # 若在大类的K-近邻中，少数类占多数，那就剔除这个多数类别的样本
        NC = NeighbourhoodCleaningRule()
        NC_data,NC_label = NC.fit_resample(raw_X,raw_y)
        return NC_data,NC_label
    elif sampling_strategy == 'InstanceHardnessThreshold' or sampling_strategy.upper() == 'IHT':
        # 默认算法是随机森林，通过分类算法给出样本阈值来剔除部分样本，（阈值较低的可以剔除）,慢
        IHT = InstanceHardnessThreshold(random_state=1)
        IHT_data,IHT_label = IHT.fit_resample(raw_X,raw_y)
        return IHT_data,IHT_label
    # hibird
    elif sampling_strategy.upper() =='SMOTEENN':
        se = SMOTEENN(random_state=1)
        se_data,se_label = se.fit_resample(raw_X,raw_y)
        return se_data,se_label
    elif sampling_strategy.upper() =='SMOTETOMEK':
        st = SMOTETomek(random_state=1)
        st_data,st_label = st.fit_resample(raw_X,raw_y)
        return st_data,st_label
    elif sampling_strategy == 'Triplets':
        print(" Triplets sampling")
        tpl = Triplets()
        tpl_data,tpl_label = tpl.fit_resample(raw_X,raw_y)
        return tpl_data,tpl_label
    else :
        print("skipped all the sampling strategy,but return the raw data and label")
        return raw_X,raw_y
# ['kmeans','spectral','kmeans++','kmedoids','OPTICS','meanshift','gmm']
def inremental_sampling(prototype_map,raw_X,raw_y,cluster_strategy):
    class_nums = len(np.unique(raw_y))
    print("class nums" ,class_nums)
    if cluster_strategy == 'ros-p' or cluster_strategy == 'ros-h' or cluster_strategy=='tpl':
        isap = Incremental_sampling2()
        resampling_data,resampling_label,prototype_map = isap.fit(new_data=raw_X,new_data_label=raw_y,last_round_prototype=prototype_map,sampling_strategy=cluster_strategy)
    else :
        isap = IncrementalSampling(cluster_strategy=cluster_strategy)
        resampling_data,resampling_label,prototype_map = isap.fit(incremental_prototype_map=prototype_map,data=raw_X,label=raw_y)
    return resampling_data,resampling_label,prototype_map
# ['kmeans','spectral','kmeans++','kmedoids','OPTICS','meanshift','gmm']
def read_data_return_tensor(dataset_path, round_id, client_id, sampling_strategy='no',prototype_map = {},cluster_strategy='kmeans'):
    folder_path = os.path.join(dataset_path, f'client_{client_id}')
    if not os.path.exists(folder_path):
        os.makedirs(folder_path)
    open_file_path = os.path.join(folder_path, f'round_{round_id}.csv')
    data = pd.read_csv(open_file_path, header=0)
    # 排除标题行并打乱数据
    data_shuffled = shuffle(data)  # 排除标题行并打乱数据

    # 提取特征和目标变量
    raw_X = data_shuffled.iloc[:, :-1].values  # 特征
    raw_y = data_shuffled.iloc[:, -1].values   # 目标变量
    raw_y = raw_y.astype(float)
    # print(len(raw_X),type(raw_X))
    # print(len(raw_X),type(raw_X))
    if sampling_strategy == 'IncrementalSampling':
        print("using IncrementalSampling")
        resampling_X,resampling_y,prototype_map = inremental_sampling(prototype_map,raw_X,raw_y,cluster_strategy=cluster_strategy)
    else:
        resampling_X,resampling_y = data_sampling(raw_X,raw_y,sampling_strategy)
        resampling_y.astype(float)
    resampling_X = np.array(resampling_X)  # 将列表转换为单个NumPy数组
    resampling_y = np.array(resampling_y)  # 将列表转换为单个NumPy数组

    X_train_tensor = torch.tensor(resampling_X, dtype=torch.float32)  # 特征张量
    y_train_tensor = torch.tensor(resampling_y, dtype=torch.long)   # 标签张量
    return X_train_tensor,y_train_tensor,prototype_map
def read_test_data(test_data_path):
    data = pd.read_csv(test_data_path, header=0)
    # 排除标题行并打乱数据
    data_shuffled = shuffle(data)  # 排除标题行并打乱数据

    # 提取特征和目标变量
    X = data_shuffled.iloc[:, :-1].values.astype(float)  # 特征
    # print(X)
    y = data_shuffled.iloc[:, -1].values   # 目标变量
    y = y.astype(float)

    X_test_tensor = torch.tensor(X, dtype=torch.float32)  # 特征张量
    y_test_tensor = torch.tensor(y, dtype=torch.long)   # 标签张量
    return X_test_tensor,y_test_tensor


In [ ]:
def aggregate_fednova(local_params_list,gm):
    # (share_params(clients_models[i]),coeff, norm_grad, data_len) as input
    total_data_len = sum(data_len for _, _, _, data_len in local_params_list)
    global_model_state = gm.state_dict()
    nova_model_state = copy.deepcopy(global_model_state)
    # avg_loss = 0
    coeff = 0.0
    for clientID,(client_model,client_coeff,client_norm_grad,client_local_data_len) in enumerate(local_params_list):
        coeff = coeff + client_coeff*client_local_data_len/total_data_len
        for key in client_model.state_dict():
            if clientID == 0:
                nova_model_state[key] = client_norm_grad[key] * client_local_data_len/total_data_len
            else:
                nova_model_state[key] =nova_model_state[key]+ client_norm_grad[key] * client_local_data_len/total_data_len
        # avg_loss = avg_loss + cl
    for key in global_model_state:
        global_model_state[key] -= coeff*nova_model_state[key]

    return global_model_state
pp = []
def runFedNova(samplingName,settingName,cluster_strategy):
    sampling_strategy_name = samplingName
    num_clients = 10
    # 初始化全局模型和客户端模型
    input_size = 8
    hidden_size = 100
    output_size = 2
    global_model = MLP(input_size, hidden_size, output_size)
    client_prototype_map = [{} for _ in range(num_clients)]
    clients_models = [MLP(input_size, hidden_size, output_size) for _ in range(num_clients)]

    num_epochs = 400
    num_global_updates = 36
    # 'E:/FedStream/real_data_set/realdataset0427/elecNorm/Electricity_client_random/'
    base_path ='E:/FedStream/' # 'E:/FedStream/'
    dataset_name = 'elecNorm'
    setting_name = settingName # 'CovA_Abrupt_BtoVH'

    algorithm = 'FedNova_kvalue30'
    experiment_times = 'epoch200'
    save_loss_path = f'{base_path}/loss/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}kdt_{experiment_times}'
    save_model_path = f'{base_path}/models/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}kdt_{experiment_times}'
    save_metrics_path  = f'{base_path}/metrics/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}kdt_{experiment_times}'
    # E:\FedStream\real_data_set\realdataset0427\covertypeNorm\CoverType_client_Full_class
    read_data_path = f'E:/FedStream/real_data_set/realdataset0427/{dataset_name}/{setting_name}/'
    # 读取测试集CSV文件并转换为PyTorch张量
    # E:\FedStream\real_data_set\realdataset0427\covertypeNorm
    test_path = 'E:/FedStream/real_data_set/realdataset0427/elecNorm/test_dataset.csv'
    X_test_tensor,y_test_tensor = read_test_data(test_path)

    for update in range(num_global_updates):
        print(f"round{update}")
        local_params_list = []

        for i in range(num_clients):
            # 在每个客户端训练本地模型
            print(f"client{i}")
            X_train_local,y_train_local,prototype_map_r = read_data_return_tensor(read_data_path,round_id=update,client_id=i,sampling_strategy=sampling_strategy_name,prototype_map=client_prototype_map[i],cluster_strategy=cluster_strategy)
            client_prototype_map[i] = prototype_map_r
            # 训练本地模型并获取损失值
            losses, coeff, norm_grad, data_len = train_model_FedNova_local(clients_models[i],X_train_local,y_train_local,num_epochs=num_epochs)
            # y_train_tensor = torch.sub(y_train_tensor, 1)
            # losses, coeff, norm_grad, data_len = train_model_FedNova_local(clients_models[i],X_train_local,torch.sub(y_train_local, 1),num_epochs=num_epochs)
            # save_loss(loss_list=losses,client_id=i,round_id=update,save_loss_path=save_loss_path)

            local_metrics = test(copy.deepcopy(clients_models[i]),X_test_tensor,y_test_tensor)
            local_params_list.append((copy.deepcopy(clients_models[i]),coeff, norm_grad, data_len))
            save_metrics(title=f"client_{i}_metrics", rounds=update, metrics=local_metrics,save_folder = save_metrics_path)

        aggregated_params = aggregate_fednova(local_params_list,gm = copy.deepcopy(global_model))
        global_model.load_state_dict(aggregated_params)

        # 在每轮结束后发送全局模型参数给客户端
        gm = copy.deepcopy(global_model)
        save_model(copy.deepcopy(gm),update,save_model_path)
        for client_model in clients_models:
            client_model.load_state_dict(gm.state_dict())

        me = test(gm,X_test_tensor,y_test_tensor) # torch.sub(y_train_tensor, 1)
        # me = test(gm,X_test_tensor,torch.sub(y_test_tensor, 1))
        save_metrics(title="global_back", rounds=update, metrics=me,save_folder = save_metrics_path)
        print("gme acc:" ,me)

def train_model_FedReweight_local(input_model, X_train_tensor, y_train_tensor, num_epochs):
    losses = []
    model = copy.deepcopy(input_model)
    optimizer = optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.CrossEntropyLoss()
    global_weights = copy.deepcopy(list(model.parameters()))

    model.train()
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        loss.backward()
        optimizer.step()

        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())

    prox_term = 0.0
    for p_i, param in enumerate(model.parameters()):
        prox_term += torch.norm(param - global_weights[p_i]) ** 2
    print("prox_term : ",prox_term.item())
    return copy.deepcopy(model.state_dict()), prox_term.item(), losses
def aggregate_fedReweight(local_params_list, prox_terms):
    """
    聚合本地模型参数。

    参数:
    local_params_list: List[Dict[str, torch.Tensor]]
        每个元素是一个本地模型参数字典。
    prox_terms: List[float]
        每个本地模型的prox_term列表。

    返回:
    global_model_params: Dict[str, torch.Tensor]
        聚合后的全局模型参数字典。
    """
    # 初始化全局模型参数
    global_model_params = {key: torch.zeros_like(param) for key, param in local_params_list[0].items()}

    # 计算权重的倒数
    inv_prox_terms = [1.0 / (term + 1e-10) for term in prox_terms]

    # 归一化权重的倒数
    total_inv_weight = sum(inv_prox_terms)
    normalized_weights = [inv_weight / total_inv_weight for inv_weight in inv_prox_terms]

    # 聚合模型参数
    for key in global_model_params.keys():
        for local_params, weight in zip(local_params_list, normalized_weights):
            global_model_params[key] += weight * local_params[key]

    return global_model_params
def runFedReweight(samplingName, settingName, cluster_strategy):
    sampling_strategy_name=samplingName
    num_clients = 10
    # 初始化全局模型和客户端模型
    input_size = 8
    hidden_size = 100
    output_size = 2
    global_model = MLP(input_size, hidden_size, output_size)
    client_prototype_map = [{} for _ in range(num_clients)]
    clients_models = [MLP(input_size, hidden_size, output_size) for _ in range(num_clients)]

    num_epochs = 400
    num_global_updates = 36
    # 'E:/FedStream/real_data_set/realdataset0427/elecNorm/Electricity_client_random/'
    base_path ='E:/FedStream/' # 'E:/FedStream/'
    dataset_name = 'elecNorm'
    setting_name = settingName # 'CovA_Abrupt_BtoVH'
    algorithm = 'FedReweight_kvalue30'
    experiment_times = 'epoch200'
    save_loss_path = f'{base_path}/loss/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}fa_{experiment_times}'
    save_model_path = f'{base_path}/models/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}fa_{experiment_times}'
    save_metrics_path = f'{base_path}/metrics/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}_{cluster_strategy}fa_{experiment_times}'
    read_data_path = f'E:/FedStream/real_data_set/realdataset0427/{dataset_name}/{setting_name}/'
    test_path = 'E:/FedStream/real_data_set/realdataset0427/elecNorm/test_dataset.csv'
    X_test_tensor, y_test_tensor = read_test_data(test_path)

    for update in range(num_global_updates):
        print(f"round{update}")
        local_params_list = []
        prox_terms = []

        for i in range(num_clients):
            print(f"client{i}")
            X_train_local, y_train_local, prototype_map_r = read_data_return_tensor(
                read_data_path, round_id=update, client_id=i,
                sampling_strategy=sampling_strategy_name, prototype_map=client_prototype_map[i], cluster_strategy=cluster_strategy
            )
            client_prototype_map[i] = prototype_map_r
            local_params, prox_term, losses = train_model_FedReweight_local(
                clients_models[i], X_train_local, y_train_local, num_epochs=num_epochs
            )
            local_metrics = test(copy.deepcopy(clients_models[i]), X_test_tensor, y_test_tensor)
            local_params_list.append(local_params)
            prox_terms.append(prox_term)
            save_metrics(f"client_{i}_metrics", update, local_metrics, save_metrics_path)

        aggregated_params = aggregate_fedReweight(local_params_list, prox_terms)
        global_model.load_state_dict(aggregated_params)

        gm = copy.deepcopy(global_model)
        save_model(gm, update, save_model_path)
        for client_model in clients_models:
            client_model.load_state_dict(gm.state_dict())

        global_metrics = test(gm, X_test_tensor, y_test_tensor)
        save_metrics("global_back", update, global_metrics, save_metrics_path)
        print("gme acc:", global_metrics)

import time

dataset_list = ['Electricity_client_random','Electricity_client_random','Electricity_client_random','Electricity_client_random','Electricity_client_random']
cluster_strategy_list = ['ros-p','kmeans','gmm','kmeans++','OPTICS','meanshift','ros-h','tpl']

total_start_time = time.time()  # 记录整个循环的开始时间
ex_time_list = []
import gc
for j, settingname in enumerate(dataset_list):
    for i, cluster_strategy in enumerate(cluster_strategy_list):
        start_time = time.time()  # 记录当前迭代的开始时间
        runFedReweight(samplingName='IncrementalSampling', settingName=settingname,cluster_strategy=cluster_strategy)
        end_time = time.time()  # 记录当前迭代的结束时间
        execution_time = end_time - start_time  # 计算当前迭代的执行时间
        ex_time_list.append(execution_time)
        gc.collect()
        time.sleep(10)
        runFedNova(samplingName='IncrementalSampling', settingName=settingname,cluster_strategy=cluster_strategy)
        end_time = time.time()  # 记录当前迭代的结束时间
        execution_time = end_time - start_time  # 计算当前迭代的执行时间
        ex_time_list.append(execution_time)
        gc.collect()
        time.sleep(10)
total_end_time = time.time()  # 记录整个循环的结束时间
total_execution_time = total_end_time - total_start_time  # 计算整个循环的执行时间

"""
Total execution time: 43781.61214756966 seconds
[361.5998156070709, 695.8967483043671, 1122.2329652309418, 1491.8523399829865, 2041.0847158432007, 245.79230976104736, 519.3722066879272, 804.5987689495087, 1096.8735597133636, 1578.1041350364685, 204.54272198677063, 473.8825399875641, 752.6243813037872, 1025.656091451645, 1495.5170149803162, 255.38020205497742, 551.6957035064697, 851.6537253856659, 1149.5674242973328, 1676.0919296741486, 217.40776872634888, 423.3815858364105, 658.1962721347809, 896.0590415000916, 1267.3063640594482, 198.13956332206726, 426.0759596824646, 663.6414759159088, 909.7201945781708, 1322.9295241832733, 323.3573501110077, 675.2849390506744, 1013.061957359314, 1342.9524464607239, 1841.935760974884, 217.272212266922, 451.73141074180603, 688.7585217952728, 930.3877067565918, 1332.9261558055878, 194.69750785827637, 406.1672217845917, 624.3995325565338, 828.4607467651367, 1223.8081316947937, 217.2660939693451, 444.29296016693115, 692.586208820343, 920.2769691944122, 1330.5964970588684, 219.8984398841858, 454.6786720752716, 693.4187605381012, 936.2140798568726, 1350.6209127902985, 226.85436344146729, 441.10340118408203, 667.992844581604, 875.9118542671204, 1261.3624713420868, 301.4935345649719, 643.937819480896, 1003.7212455272675, 1401.4035060405731, 1907.6885023117065, 232.2831780910492, 455.81967186927795, 698.3762543201447, 917.6773438453674, 1347.5765206813812, 190.8495798110962, 415.3082528114319, 640.4189343452454, 855.5775063037872, 1242.2792418003082, 213.75201511383057, 441.7514078617096, 680.9132573604584, 921.5076911449432, 1397.4388468265533, 225.6622929573059, 467.8324189186096, 710.6045339107513, 966.1795434951782, 1412.0875179767609, 215.28059244155884, 445.5932228565216, 667.8729038238525, 934.6181786060333, 1330.4306797981262, 298.0329484939575, 610.7048373222351, 951.8706934452057, 1270.3417372703552, 1782.8591928482056, 222.06331539154053, 465.27199125289917, 711.9037458896637, 943.0039372444153, 1341.4884932041168, 207.03163862228394, 415.7807939052582, 639.3788909912109, 835.0146827697754, 1228.2939958572388, 222.09649920463562, 476.3372075557709, 716.7719995975494, 956.5898215770721, 1372.6015484333038, 217.3429172039032, 449.26846861839294, 702.0598134994507, 931.8860130310059, 1351.4647755622864, 217.9827220439911, 433.7823917865753, 673.4863579273224, 896.4204590320587, 1310.755215883255, 313.2643916606903, 674.4342362880707, 1035.4926853179932, 1368.869577884674, 1883.9467177391052, 248.70469880104065, 485.3929476737976, 748.4397675991058, 983.9063296318054, 1411.3423051834106, 218.15851831436157, 443.4967737197876, 668.0506916046143, 887.9111087322235, 1279.1134011745453, 247.8854467868805, 496.07720255851746, 741.0149195194244, 973.8983969688416, 1385.7055547237396, 246.1520254611969, 493.6700098514557, 748.0011239051819, 999.0514359474182, 1424.6116309165955, 247.97842979431152, 470.54117941856384, 707.2244086265564, 931.2747294902802, 1344.6901519298553]
cluster_strategy_list = ['ros-p','kmeans','gmm','kmeans++','OPTICS','meanshift','ros-h','tpl']
Total execution time: 45350.00229358673 seconds
[604.0159723758698, 1608.9409210681915, 308.8475351333618, 630.5081701278687, 229.77253127098083, 505.2797465324402, 329.4480764865875, 662.87797498703, 267.64796233177185, 558.8816602230072, 1334.3113934993744, 2123.216650247574, 864.4599211215973, 1814.4137480258942, 1041.8025891780853, 2012.9174418449402, 737.4796991348267, 1476.0368378162384, 239.51131296157837, 483.6601929664612, 177.72996068000793, 374.01590847969055, 242.32983899116516, 480.6908302307129, 200.56763982772827, 422.36154079437256, 1522.275984287262, 3065.997274160385, 1139.1349482536316, 2359.986419200897, 1110.6189634799957, 1880.6100525856018, 907.4883480072021, 1677.252196073532, 288.2540605068207, 561.1427917480469, 211.73172211647034, 455.31998920440674, 286.9322054386139, 583.9369330406189, 244.06311202049255, 511.74602818489075, 1520.8277351856232, 3337.975736618042, 445.51049160957336, 1033.9422578811646, 638.6830837726593, 1349.4666216373444, 638.5774877071381, 1358.714810371399, 203.95747876167297, 436.16390204429626, 162.14799094200134, 342.309609413147, 211.21540331840515, 424.31862473487854, 186.29776859283447, 381.5432138442993, 986.0239462852478, 1958.8585393428802, 744.1172997951508, 1456.766506433487, 652.5195784568787, 1394.9515311717987, 602.7161254882812, 1139.0476672649384, 214.25831127166748, 460.6822681427002, 174.83011317253113, 357.7395453453064, 210.5268087387085, 426.61856865882874, 177.8408498764038, 365.9589161872864, 851.4238648414612, 1794.6692702770233, 618.2231488227844, 1331.2653946876526, 668.7076387405396, 1346.1363518238068]
"""
print(f"Total execution time: {total_execution_time} seconds")
print(ex_time_list)


In [12]:
def aggregate_fednova(local_params_list,gm):
    # (share_params(clients_models[i]),coeff, norm_grad, data_len) as input
    total_data_len = sum(data_len for _, _, _, data_len in local_params_list)
    global_model_state = gm.state_dict()
    nova_model_state = copy.deepcopy(global_model_state)
    # avg_loss = 0
    coeff = 0.0
    for clientID,(client_model,client_coeff,client_norm_grad,client_local_data_len) in enumerate(local_params_list):
        coeff = coeff + client_coeff*client_local_data_len/total_data_len
        for key in client_model.state_dict():
            if clientID == 0:
                nova_model_state[key] = client_norm_grad[key] * client_local_data_len/total_data_len
            else:
                nova_model_state[key] =nova_model_state[key]+ client_norm_grad[key] * client_local_data_len/total_data_len
        # avg_loss = avg_loss + cl
    for key in global_model_state:
        global_model_state[key] -= coeff*nova_model_state[key]

    return global_model_state
pp = []
def runFedNova(samplingName,settingName,cluster_strategy):
    sampling_strategy_name = samplingName
    num_clients = 10
    # 初始化全局模型和客户端模型
    input_size = 10
    hidden_size = 100
    output_size = 2
    global_model = MLP(input_size, hidden_size, output_size)
    client_prototype_map = [{} for _ in range(num_clients)]
    clients_models = [MLP(input_size, hidden_size, output_size) for _ in range(num_clients)]

    num_epochs = 200
    num_global_updates = 100
    base_path = 'E:/FedStream/'
    dataset_name = '130K_binary_client'
    setting_name = settingName # 'CovA_Abrupt_BtoVH'
    sampling_strategy_name = samplingName

    algorithm = 'FedNova_kvalue30'
    experiment_times = 'epoch200'
    save_loss_path = f'{base_path}/loss/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_model_path = f'{base_path}/models/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_metrics_path  = f'{base_path}/metrics/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    read_data_path = f'E:/FedStream/data_set_syn/Synthetic0310/Make_CF/Syn130K_10F_2C/{dataset_name}/{setting_name}/'
    # 读取测试集CSV文件并转换为PyTorch张量
    test_path = 'E:/FedStream/data_set_syn/Synthetic0310/Make_CF/Syn130K_10F_2C/test/test.csv'
    X_test_tensor,y_test_tensor = read_test_data(test_path)

    for update in range(num_global_updates):
        print(f"round{update}")
        local_params_list = []

        for i in range(num_clients):
            # 在每个客户端训练本地模型
            print(f"client{i}")
            X_train_local,y_train_local,prototype_map_r = read_data_return_tensor(read_data_path,round_id=update,client_id=i,sampling_strategy=sampling_strategy_name,prototype_map=client_prototype_map[i],cluster_strategy=cluster_strategy)
            client_prototype_map[i] = prototype_map_r
            # 训练本地模型并获取损失值
            losses, coeff, norm_grad, data_len = train_model_FedNova_local(clients_models[i],X_train_local,y_train_local,num_epochs=num_epochs)
            # y_train_tensor = torch.sub(y_train_tensor, 1)
            # losses, coeff, norm_grad, data_len = train_model_FedNova_local(clients_models[i],X_train_local,torch.sub(y_train_local, 1),num_epochs=num_epochs)
            # save_loss(loss_list=losses,client_id=i,round_id=update,save_loss_path=save_loss_path)

            local_metrics = test(copy.deepcopy(clients_models[i]),X_test_tensor,y_test_tensor)
            local_params_list.append((copy.deepcopy(clients_models[i]),coeff, norm_grad, data_len))
            save_metrics(title=f"client_{i}_metrics", rounds=update, metrics=local_metrics,save_folder = save_metrics_path)

        aggregated_params = aggregate_fednova(local_params_list,gm = copy.deepcopy(global_model))
        global_model.load_state_dict(aggregated_params)

        # 在每轮结束后发送全局模型参数给客户端
        gm = copy.deepcopy(global_model)
        save_model(copy.deepcopy(gm),update,save_model_path)
        for client_model in clients_models:
            client_model.load_state_dict(gm.state_dict())

        me = test(gm,X_test_tensor,y_test_tensor) # torch.sub(y_train_tensor, 1)
        # me = test(gm,X_test_tensor,torch.sub(y_test_tensor, 1))
        save_metrics(title="global_back", rounds=update, metrics=me,save_folder = save_metrics_path)
        print("gme acc:" ,me)

def train_model_FedReweight_local(input_model, X_train_tensor, y_train_tensor, num_epochs):
    losses = []
    model = copy.deepcopy(input_model)
    optimizer = optim.SGD(model.parameters(), lr=0.01)
    criterion = nn.CrossEntropyLoss()
    global_weights = copy.deepcopy(list(model.parameters()))

    model.train()
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        loss.backward()
        optimizer.step()

        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())

    prox_term = 0.0
    for p_i, param in enumerate(model.parameters()):
        prox_term += torch.norm(param - global_weights[p_i]) ** 2
    print("prox_term : ",prox_term.item())
    return copy.deepcopy(model.state_dict()), prox_term.item(), losses
def aggregate_fedReweight(local_params_list, prox_terms):
    """
    聚合本地模型参数。

    参数:
    local_params_list: List[Dict[str, torch.Tensor]]
        每个元素是一个本地模型参数字典。
    prox_terms: List[float]
        每个本地模型的prox_term列表。

    返回:
    global_model_params: Dict[str, torch.Tensor]
        聚合后的全局模型参数字典。
    """
    # 初始化全局模型参数
    global_model_params = {key: torch.zeros_like(param) for key, param in local_params_list[0].items()}

    # 计算权重的倒数
    inv_prox_terms = [1.0 / (term + 1e-10) for term in prox_terms]

    # 归一化权重的倒数
    total_inv_weight = sum(inv_prox_terms)
    normalized_weights = [inv_weight / total_inv_weight for inv_weight in inv_prox_terms]

    # 聚合模型参数
    for key in global_model_params.keys():
        for local_params, weight in zip(local_params_list, normalized_weights):
            global_model_params[key] += weight * local_params[key]

    return global_model_params
def runFedReweight(samplingName, settingName, cluster_strategy):

    num_clients = 10
    # 初始化全局模型和客户端模型
    input_size = 10
    hidden_size = 100
    output_size = 2
    global_model = MLP(input_size, hidden_size, output_size)
    client_prototype_map = [{} for _ in range(num_clients)]
    clients_models = [MLP(input_size, hidden_size, output_size) for _ in range(num_clients)]

    num_epochs = 200
    num_global_updates = 100
    base_path = 'E:/FedStream/'
    dataset_name = '130K_binary_client'
    setting_name = settingName # 'CovA_Abrupt_BtoVH'
    sampling_strategy_name = samplingName

    algorithm = 'FedReweight'
    experiment_times = 'epoch200'
    save_loss_path = f'{base_path}/loss/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_model_path = f'{base_path}/models/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_metrics_path  = f'{base_path}/metrics/{dataset_name}_Sampling/{algorithm}/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    read_data_path = f'E:/FedStream/data_set_syn/Synthetic0310/Make_CF/Syn130K_10F_2C/{dataset_name}/{setting_name}/'
    # 读取测试集CSV文件并转换为PyTorch张量
    test_path = 'E:/FedStream/data_set_syn/Synthetic0310/Make_CF/Syn130K_10F_2C/test/test.csv'
    X_test_tensor,y_test_tensor = read_test_data(test_path)

    for update in range(num_global_updates):
        print(f"round{update}")
        local_params_list = []
        prox_terms = []

        for i in range(num_clients):
            print(f"client{i}")
            X_train_local, y_train_local, prototype_map_r = read_data_return_tensor(
                read_data_path, round_id=update, client_id=i,
                sampling_strategy=sampling_strategy_name, prototype_map=client_prototype_map[i], cluster_strategy=cluster_strategy
            )
            client_prototype_map[i] = prototype_map_r
            local_params, prox_term, losses = train_model_FedReweight_local(
                clients_models[i], X_train_local, y_train_local, num_epochs=num_epochs
            )
            local_metrics = test(copy.deepcopy(clients_models[i]), X_test_tensor, y_test_tensor)
            local_params_list.append(local_params)
            prox_terms.append(prox_term)
            save_metrics(f"client_{i}_metrics", update, local_metrics, save_metrics_path)

        aggregated_params = aggregate_fedReweight(local_params_list, prox_terms)
        global_model.load_state_dict(aggregated_params)

        gm = copy.deepcopy(global_model)
        save_model(gm, update, save_model_path)
        for client_model in clients_models:
            client_model.load_state_dict(gm.state_dict())

        global_metrics = test(gm, X_test_tensor, y_test_tensor)
        save_metrics("global_back", update, global_metrics, save_metrics_path)
        print("gme acc:", global_metrics)

import time

dataset_list =['CovA_Abrupt_BtoH','CovA_Abrupt_BtoH','CovA_Abrupt_BtoH','CovA_Abrupt_BtoH','CovA_Abrupt_BtoH']
cluster_strategy_list = ['ros-p','kmeans','gmm','kmeans++','OPTICS','meanshift','ros-h','tpl']

total_start_time = time.time()  # 记录整个循环的开始时间
ex_time_list = []
import gc
for j, settingname in enumerate(dataset_list):
    for i, cluster_strategy in enumerate(cluster_strategy_list):
        start_time = time.time()  # 记录当前迭代的开始时间
        runFedNova(samplingName='IncrementalSampling', settingName=settingname,cluster_strategy=cluster_strategy)
        end_time = time.time()  # 记录当前迭代的结束时间
        execution_time = end_time - start_time  # 计算当前迭代的执行时间
        ex_time_list.append(execution_time)
        gc.collect()
        time.sleep(10)
        runFedReweight(samplingName='IncrementalSampling', settingName=settingname,cluster_strategy=cluster_strategy)
        end_time = time.time()  # 记录当前迭代的结束时间
        execution_time = end_time - start_time  # 计算当前迭代的执行时间
        ex_time_list.append(execution_time)
        gc.collect()
        time.sleep(10)

total_end_time = time.time()  # 记录整个循环的结束时间
total_execution_time = total_end_time - total_start_time  # 计算整个循环的执行时间

"""
Total execution time: 43781.61214756966 seconds
[361.5998156070709, 695.8967483043671, 1122.2329652309418, 1491.8523399829865, 2041.0847158432007, 245.79230976104736, 519.3722066879272, 804.5987689495087, 1096.8735597133636, 1578.1041350364685, 204.54272198677063, 473.8825399875641, 752.6243813037872, 1025.656091451645, 1495.5170149803162, 255.38020205497742, 551.6957035064697, 851.6537253856659, 1149.5674242973328, 1676.0919296741486, 217.40776872634888, 423.3815858364105, 658.1962721347809, 896.0590415000916, 1267.3063640594482, 198.13956332206726, 426.0759596824646, 663.6414759159088, 909.7201945781708, 1322.9295241832733, 323.3573501110077, 675.2849390506744, 1013.061957359314, 1342.9524464607239, 1841.935760974884, 217.272212266922, 451.73141074180603, 688.7585217952728, 930.3877067565918, 1332.9261558055878, 194.69750785827637, 406.1672217845917, 624.3995325565338, 828.4607467651367, 1223.8081316947937, 217.2660939693451, 444.29296016693115, 692.586208820343, 920.2769691944122, 1330.5964970588684, 219.8984398841858, 454.6786720752716, 693.4187605381012, 936.2140798568726, 1350.6209127902985, 226.85436344146729, 441.10340118408203, 667.992844581604, 875.9118542671204, 1261.3624713420868, 301.4935345649719, 643.937819480896, 1003.7212455272675, 1401.4035060405731, 1907.6885023117065, 232.2831780910492, 455.81967186927795, 698.3762543201447, 917.6773438453674, 1347.5765206813812, 190.8495798110962, 415.3082528114319, 640.4189343452454, 855.5775063037872, 1242.2792418003082, 213.75201511383057, 441.7514078617096, 680.9132573604584, 921.5076911449432, 1397.4388468265533, 225.6622929573059, 467.8324189186096, 710.6045339107513, 966.1795434951782, 1412.0875179767609, 215.28059244155884, 445.5932228565216, 667.8729038238525, 934.6181786060333, 1330.4306797981262, 298.0329484939575, 610.7048373222351, 951.8706934452057, 1270.3417372703552, 1782.8591928482056, 222.06331539154053, 465.27199125289917, 711.9037458896637, 943.0039372444153, 1341.4884932041168, 207.03163862228394, 415.7807939052582, 639.3788909912109, 835.0146827697754, 1228.2939958572388, 222.09649920463562, 476.3372075557709, 716.7719995975494, 956.5898215770721, 1372.6015484333038, 217.3429172039032, 449.26846861839294, 702.0598134994507, 931.8860130310059, 1351.4647755622864, 217.9827220439911, 433.7823917865753, 673.4863579273224, 896.4204590320587, 1310.755215883255, 313.2643916606903, 674.4342362880707, 1035.4926853179932, 1368.869577884674, 1883.9467177391052, 248.70469880104065, 485.3929476737976, 748.4397675991058, 983.9063296318054, 1411.3423051834106, 218.15851831436157, 443.4967737197876, 668.0506916046143, 887.9111087322235, 1279.1134011745453, 247.8854467868805, 496.07720255851746, 741.0149195194244, 973.8983969688416, 1385.7055547237396, 246.1520254611969, 493.6700098514557, 748.0011239051819, 999.0514359474182, 1424.6116309165955, 247.97842979431152, 470.54117941856384, 707.2244086265564, 931.2747294902802, 1344.6901519298553]
"""
print(f"Total execution time: {total_execution_time} seconds")
print(ex_time_list)


round0
client0
using IncrementalSampling
class nums 2
use ros p
Epoch [1/200], Loss: 0.7071
Epoch [11/200], Loss: 0.6820
Epoch [21/200], Loss: 0.6600
Epoch [31/200], Loss: 0.6406
Epoch [41/200], Loss: 0.6233
Epoch [51/200], Loss: 0.6079
Epoch [61/200], Loss: 0.5939
Epoch [71/200], Loss: 0.5812
Epoch [81/200], Loss: 0.5696
Epoch [91/200], Loss: 0.5588
Epoch [101/200], Loss: 0.5489
Epoch [111/200], Loss: 0.5396
Epoch [121/200], Loss: 0.5308
Epoch [131/200], Loss: 0.5226
Epoch [141/200], Loss: 0.5148
Epoch [151/200], Loss: 0.5074
Epoch [161/200], Loss: 0.5003
Epoch [171/200], Loss: 0.4935
Epoch [181/200], Loss: 0.4870
Epoch [191/200], Loss: 0.4807
Test Accuracy: 81.65%
client1
using IncrementalSampling
class nums 2
use ros p
Epoch [1/200], Loss: 0.7233
Epoch [11/200], Loss: 0.6993
Epoch [21/200], Loss: 0.6822
Epoch [31/200], Loss: 0.6685
Epoch [41/200], Loss: 0.6567
Epoch [51/200], Loss: 0.6460
Epoch [61/200], Loss: 0.6361
Epoch [71/200], Loss: 0.6267
Epoch [81/200], Loss: 0.6178
Epoch [9

Traceback (most recent call last):
  File "D:\ProgramData\Anaconda3\envs\python38\lib\site-packages\IPython\core\interactiveshell.py", line 3433, in run_code
    exec(code_obj, self.user_global_ns, self.user_ns)
  File "D:\AppData\Local\Temp\ipykernel_11612\134623321.py", line 213, in <module>
    runFedReweight(samplingName='IncrementalSampling', settingName=settingname,cluster_strategy=cluster_strategy)
  File "D:\AppData\Local\Temp\ipykernel_11612\134623321.py", line 179, in runFedReweight
    local_metrics = test(copy.deepcopy(clients_models[i]), X_test_tensor, y_test_tensor)
  File "D:\AppData\Local\Temp\ipykernel_11612\2932581754.py", line 701, in test
    outputs = global_model(X_test_tensor)
  File "D:\ProgramData\Anaconda3\envs\python38\lib\site-packages\torch\nn\modules\module.py", line 1194, in _call_impl
    return forward_call(*input, **kwargs)
  File "D:\AppData\Local\Temp\ipykernel_11612\2932581754.py", line 53, in forward
    x = self.relu(x)
  File "D:\ProgramData\Anac

In [ ]:
import torch
import torch.nn as nn
import copy

# 数据增强基于z-score的实现
def z_score_based_augmentation(X_train_tensor, y_train_tensor, td=3.0):
    mean = torch.mean(X_train_tensor, dim=0)
    std = torch.std(X_train_tensor, dim=0)
    z_scores = (X_train_tensor - mean) / std

    # 根据z-score进行样本增强和下采样
    augment_mask = (z_scores < -td)  # 小于ta的类别为增强类别
    downsample_mask = (z_scores > td)  # 大于td的类别为下采样类别

    return augment_mask, downsample_mask

# 调停者的实现
def mediator(X_train_tensor, y_train_tensor, augment_mask, downsample_mask):
    # 根据augment_mask和downsample_mask重新组织训练数据
    augmented_samples = X_train_tensor[augment_mask]
    downsampled_samples = X_train_tensor[downsample_mask]

    # 进行数据的重新分配和调整，具体实现根据需求进一步优化
    # 这里简化为直接返回经过augmentation和downsampling后的数据集
    return augmented_samples, downsampled_samples

def train_model_Astraea(input_model, X_train_tensor, y_train_tensor, learning_rate, num_epochs, td=3.0):
    optimizer = torch.optim.Adam(input_model.parameters(), lr=learning_rate)
    criterion = nn.CrossEntropyLoss()
    input_model.train()

    e_loss = []
    for _ in range(1, num_epochs + 1):
        train_loss = 0.0
        optimizer.zero_grad()

        # z-score based augmentation
        augment_mask, downsample_mask = z_score_based_augmentation(X_train_tensor, y_train_tensor, td=td)
        augmented_samples, downsampled_samples = mediator(X_train_tensor, y_train_tensor, augment_mask, downsample_mask)

        # 进行训练
        output = input_model(augmented_samples)
        loss = criterion(output, y_train_tensor[augment_mask])
        loss.backward()
        optimizer.step()
        train_loss += loss.item() * augmented_samples.size(0)

        train_loss = train_loss / len(augmented_samples)
        e_loss.append(train_loss)

    total_loss = sum(e_loss) / len(e_loss)
    return input_model.state_dict(), total_loss

# 参数聚合部分
def aggregate_Astraea(local_params_list, data_sizes):
    aggregated_params = {}
    total_samples = sum(data_sizes)

    for params, size in zip(local_params_list, data_sizes):
        for key in params.keys():
            if key not in aggregated_params:
                aggregated_params[key] = torch.zeros_like(params[key])
            aggregated_params[key] += params[key] * (size / total_samples)

    return aggregated_params

# Astraea算法的总体运行
def run_Astraea(num_clients, num_epochs, num_global_updates, base_path, dataset_name, setting_name, sampling_strategy_name, cluster_strategy, X_test_tensor, y_test_tensor):
    global_model = MLP(input_size, hidden_size, output_size)
    client_prototype_map = [{} for _ in range(num_clients)]
    clients_models = [MLP(input_size, hidden_size, output_size) for _ in range(num_clients)]

    save_loss_path = f'{base_path}/loss/{dataset_name}_Sampling/Astraea/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_model_path = f'{base_path}/models/{dataset_name}_Sampling/Astraea/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    save_metrics_path = f'{base_path}/metrics/{dataset_name}_Sampling/Astraea/{setting_name}/{sampling_strategy_name}/{cluster_strategy}'
    read_data_path = f'E:/FedStream/data_set_syn/Synthetic0310/Make_CF/Syn130K_10F_2C/{dataset_name}/{setting_name}/'

    for update in range(num_global_updates):
        print(f"Round {update}")
        local_params_list = []
        data_sizes = []

        for i in range(num_clients):
            print(f"Client {i}")
            X_train_local, y_train_local, prototype_map_r = read_data_return_tensor(
                read_data_path, round_id=update, client_id=i,
                sampling_strategy=sampling_strategy_name, prototype_map=client_prototype_map[i], cluster_strategy=cluster_strategy
            )
            client_prototype_map[i] = prototype_map_r
            local_params, _ = train_model_Astraea(
                clients_models[i], X_train_local, y_train_local, learning_rate=learning_rate, num_epochs=num_epochs
            )
            local_params_list.append(local_params)
            data_sizes.append(len(X_train_local))

        aggregated_params = aggregate_Astraea(local_params_list, data_sizes)
        global_model.load_state_dict(aggregated_params)

        gm = copy.deepcopy(global_model)
        save_model(gm, update, save_model_path)

        for client_model in clients_models:
            client_model.load_state_dict(gm.state_dict())

        global_metrics = test(gm, X_test_tensor, y_test_tensor)
        save_metrics("global", update, global_metrics, save_metrics_path)
        print(f"Global metrics after update {update}: {global_metrics}")

# 示例调用
run_Astraea(num_clients=10, num_epochs=200, num_global_updates=100, base_path='E:/FedStream/', dataset_name='130K_binary_client', setting_name='CovA_Abrupt_BtoVH', sampling_strategy_name='your_sampling_strategy', cluster_strategy='your_cluster_strategy', X_test_tensor=X_test_tensor, y_test_tensor=y_test_tensor)


In [ ]:
def train_client_model_Astraea(input_model, X_train_tensor, y_train_tensor, num_epochs):
    learning_rate = 0.01
    optimizer = torch.optim.Adam(input_model.parameters(), lr=learning_rate)
    criterion = nn.CrossEntropyLoss()
    input_model.train()
    losses = []
    for epoch in range(num_epochs):
        optimizer.zero_grad()
        outputs = input_model(X_train_tensor)
        loss = criterion(outputs, y_train_tensor)
        loss.backward()
        optimizer.step()
        if epoch % 10 == 0:
            print(f"Epoch [{epoch+1}/{num_epochs}], Loss: {loss.item():.4f}")
        losses.append(loss.item())
    return input_model.state_dict(), losses
def HyBridFL(model, rounds):
    global_weights = model.state_dict()
    nums_client = 10
    # 全局更新轮数
    for i in range(rounds):
        print(f"\nGLOBAL ROUND {i}")
        temp_weights, temp_datasizes = [], []
        # 遍历每一个Edge
        for j in range(nums_client):
            # 模型分发
            TotalEdges[j].edgeUpdate(model=copy.deepcopy(model))
            edge_weights, edge_datasize = TotalEdges[j].edgeAggregation()
            temp_weights.append(copy.deepcopy(edge_weights))
            temp_datasizes.append(edge_datasize)
        # Edge端聚合
        sumOfTempDatasizes = sum(temp_datasizes)
        weights_global_avg = copy.deepcopy(temp_weights[0])
        for key in weights_global_avg.keys():
            weights_global_avg[key] *= temp_datasizes[0]/sumOfTempDatasizes
        for key in weights_global_avg.keys():
            for k in range(1, len(temp_weights)):
                ratio = temp_datasizes[k]/sumOfTempDatasizes
                # print(f"Edge#{k} this turn datasize ratio {ratio} across all edges")
                weights_global_avg[key] += temp_weights[k][key]*ratio

            # weights_global_avg[key] = torch.div(weights_global_avg[key], len(temp_weights))

        global_weights = weights_global_avg
        print('\n')
        model.load_state_dict(weights_global_avg)